In [1]:
from pubnub.pnconfiguration import PNConfiguration
from pubnub.enums import PNHeartbeatNotificationOptions
from pubnub.pubnub import PubNub
pn_configuration = PNConfiguration()
# subscribe_key from Admin Portal
pn_configuration.subscribe_key = "sub-c-8f1bdfa2-f7d8-4004-9d34-e78edfa70fa0"
# publish_key from Admin Portal (only required if publishing)
pn_configuration.publish_key = "pub-c-a4f1498a-4df7-496b-98a4-ec2e72e48f34"
# secret_key (only required for modifying/revealing access permissions)
pn_configuration.secret_key = "sec-c-ZmVkODhiZGQtZmYzNC00NDEzLWFhYzUtYjIwMTg2YTIzYTg4"

pnconfig = PNConfiguration()
pnconfig.subscribe_key = "sub-c-8f1bdfa2-f7d8-4004-9d34-e78edfa70fa0"
pnconfig.publish_key = "pub-c-a4f1498a-4df7-496b-98a4-ec2e72e48f34"
pnconfig.ssl = True
pnconfig.secret_key = "sec-c-ZmVkODhiZGQtZmYzNC00NDEzLWFhYzUtYjIwMTg2YTIzYTg4"
pnconfig.user_id = "mishal0404"
pubnub = PubNub(pnconfig)
def publish_callback(result, status):
  print("result= ",result)
  print("status= ", status)

def sendlanes(data):
        pubnub.publish().channel("lane").message(data).pn_async(publish_callback)


In [2]:
from confluent_kafka import Consumer, KafkaException
import pandas as pd
import json
import datetime
import time

conf = {
    'bootstrap.servers': 'ec2-65-0-72-75.ap-south-1.compute.amazonaws.com:9092', 
    'group.id': 'my-group',  
}


consumer = Consumer(conf)

BIG = 1800
SMALL = 600
consumer.subscribe(['IOTTemperatureStream01'])


df = pd.DataFrame(columns = ["plant_name", "lane_number", "timestamp", "temperature", "component_type"])


highest = {}
count = 0
lis = []
while True:
    
    msg = consumer.poll(1.0)
    if msg is None:
        print("none")
        continue
    if msg.error():
        raise KafkaException(msg.error())

    msgstr = msg.value().decode('utf-8')
    msgdic = json.loads(msgstr)
    reqvalues = {"name":msgdic.get('plant_name', ""), "lane":msgdic.get('lane_number', ""), "time":msgdic.get('timestamp', None), "temp":msgdic.get('temperature', None), "componenttype":msgdic["component_info"].get("component_type", None)}
    #print(reqvalues)
    count=count+1
    print(count)


    tempgreaterthan50 = {}
    lanedict = {}
    lis.append(reqvalues)
    #print(lis)
    if count>=BIG:
        lis.pop(0)
        

        for reqvalues in lis[-1:-SMALL-1:-1]:
            if reqvalues["temp"] and reqvalues["componenttype"]:
                if float(reqvalues["temp"])>50:
                    tempgreaterthan50[reqvalues["componenttype"]] = float(reqvalues["temp"])
                    
                if reqvalues["temp"] and reqvalues["componenttype"]:
                    if reqvalues["lane"]+reqvalues["componenttype"] not in lanedict:
                            lanedict[reqvalues["lane"]+reqvalues["componenttype"]] = float(reqvalues["temp"])
                    else:
                            if float(reqvalues["temp"]) > lanedict[reqvalues["lane"]+reqvalues["componenttype"]]:
                                lanedict[reqvalues["lane"]+reqvalues["componenttype"]] = float(reqvalues["temp"])

        for reqvalues in lis[0:BIG-SMALL+1]:
            if reqvalues["temp"] and reqvalues["componenttype"]:
                if reqvalues["lane"]+reqvalues["componenttype"] not in lanedict:
                        lanedict[reqvalues["lane"]+reqvalues["componenttype"]] = float(reqvalues["temp"])
                else:
                        if float(reqvalues["temp"]) > lanedict[reqvalues["lane"]+reqvalues["componenttype"]]:
                            lanedict[reqvalues["lane"]+reqvalues["componenttype"]] = float(reqvalues["temp"])

    elif count>=SMALL:
        for reqvalues in lis[-1:-SMALL-1:-1]:
            if reqvalues["temp"] and reqvalues["componenttype"]:
                if float(reqvalues["temp"])>50:
                    tempgreaterthan50[reqvalues["componenttype"]] = float(reqvalues["temp"])
    
    lanedict.update(tempgreaterthan50)
    if len(tempgreaterthan50)+len(lanedict)>0:
        print("temp= ",tempgreaterthan50)
        print("lanedata= ", lanedict)
        sendlanes(lanedict)
            


1
2
3
4
5
6
7
8
9
10
11
12
13
14
15
16
17
18
19
20
21
22
23
24
25
26
27
28
29
30
31
32
33
34
35
36
37
38
39
40
41
42
43
44
45
46
47
48
49
50
51
52
53
54
55
56
57
58
59
60
61
62
63
64
65
66
67
68
69
70
71
72
73
74
75
76
77
78
79
80
81
82
83
84
85
86
87
88
89
90
91
92
93
94
95
96
97
98
99
100
101
102
103
104
105
106
107
108
109
110
111
112
113
114
115
116
117
118
119
120
121
122
123
124
125
126
127
128
129
130
131
132
133
134
135
136
137
138
139
140
141
142
143
144
145
146
147
148
149
150
151
152
153
154
155
156
157
158
159
160
161
162
163
164
165
166
167
168
169
170
171
172
173
174
175
176
177
178
179
180
181
182
183
184
185
186
187
188
189
190
191
192
193
194
195
196
197
198
199
200
201
202
203
204
205
206
207
208
209
210
211
212
213
214
215
216
217
218
219
220
221
222
223
224
225
226
227
228
229
230
231
232
233
234
235
236
237
238
239
240
241
242
243
244
245
246
247
248
249
250
251
252
253
254
255
256
257
258
259
260
261
262
263
264
265
266
267
268
269
270
271
272
273
274
275
276
277


KeyboardInterrupt: 